In [1]:
import requests
import os
import datetime
import time
import random
import hashlib
from pydrive.auth import GoogleAuth
from pydrive.drive import GoogleDrive

In [3]:
ESP32_IP = "192.168.10.114"
IMAGE_URL = f"http://{ESP32_IP}/image"
SAVE_DIR = "images"
GOOGLE_DRIVE_FOLDER_ID = "1j-JN4hXzCYdJ7iE1mYVw--ezV-WDLH6k"

gauth = GoogleAuth()
gauth.LocalWebserverAuth()
drive = GoogleDrive(gauth)

Your browser has been opened to visit:

    https://accounts.google.com/o/oauth2/auth?client_id=135516510394-i0mhns9iba2ajrhjudnfqnochlpse29a.apps.googleusercontent.com&redirect_uri=http%3A%2F%2Flocalhost%3A8080%2F&scope=https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive&access_type=offline&response_type=code

Authentication successful.


In [5]:
if not os.path.exists(SAVE_DIR):
    os.makedirs(SAVE_DIR)

last_image_hash = None  # Store the hash of the last uploaded image

def retry(operation, retries=3, base_delay=2, on_exception=Exception):
    for attempt in range(1, retries + 1):
        try:
            return operation()
        except on_exception as e:
            print(f"[Retry {attempt}] Error: {e}")
            time.sleep(base_delay * attempt + random.uniform(0, 1))
    print(f"[FAIL] Operation failed after {retries} attempts.")
    return None

def compute_hash(filepath):
    sha = hashlib.sha256()
    with open(filepath, "rb") as f:
        for chunk in iter(lambda: f.read(4096), b""):
            sha.update(chunk)
    return sha.hexdigest()

def fetch_image():
    timestamp = datetime.datetime.now().strftime("%Y%m%d_%H%M%S")
    image_path = os.path.join(SAVE_DIR, f"esp32_image_{timestamp}.jpg")

    def do_fetch():
        print("Fetching image from ESP32...")
        response = requests.get(IMAGE_URL, headers={"Accept": "image/jpeg"}, stream=True, timeout=10)
        if response.status_code != 200:
            raise RuntimeError(f"Failed to fetch image, status {response.status_code}")

        content_type = response.headers.get("Content-Type", "")
        if "image/jpeg" not in content_type:
            raise RuntimeError(f"Invalid content type: {content_type}")

        with open(image_path, "wb") as file:
            for chunk in response.iter_content(chunk_size=4096):
                if chunk:
                    file.write(chunk)

        print(f"Image saved to {image_path}")
        return image_path

    return retry(do_fetch)

def upload_image(image_path):
    def do_upload():
        print("Uploading to Google Drive...")
        file_drive = drive.CreateFile({'title': os.path.basename(image_path), 'parents': [{'id': GOOGLE_DRIVE_FOLDER_ID}]})
        file_drive.SetContentFile(image_path)
        file_drive.Upload()
        print(f"Uploaded: {image_path}")
        return True

    success = retry(do_upload)
    if success and os.path.exists(image_path):
        os.remove(image_path)
        print(f"Deleted local file: {image_path}")

# Main loop
while True:
    path = fetch_image()
    if path:
        img_hash = compute_hash(path)
        if img_hash == last_image_hash:
            print("Image is identical to previous. Skipping upload.")
            os.remove(path)
        else:
            last_image_hash = img_hash
            upload_image(path)
    else:
        print("Skipping upload due to fetch failure.")

    time.sleep(10)

Fetching image from ESP32...
[Retry 1] Error: HTTPConnectionPool(host='192.168.10.114', port=80): Max retries exceeded with url: /image (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x157f82a10>: Failed to establish a new connection: [Errno 61] Connection refused'))
Fetching image from ESP32...
[Retry 2] Error: HTTPConnectionPool(host='192.168.10.114', port=80): Max retries exceeded with url: /image (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x157fa4bd0>: Failed to establish a new connection: [Errno 61] Connection refused'))
Fetching image from ESP32...
[Retry 3] Error: HTTPConnectionPool(host='192.168.10.114', port=80): Max retries exceeded with url: /image (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x157f82c10>: Failed to establish a new connection: [Errno 61] Connection refused'))
[FAIL] Operation failed after 3 attempts.
Skipping upload due to fetch failure.
Fetching image from ESP32...


KeyboardInterrupt: 